In [1]:
import re 

def preprocess_minutes(minutes):

    pos = re.search('(.?국내외\s?경제\s?동향.?과 관련하여,?|\(가\).+경제전망.*|\(가\) 국내외 경제동향 및 평가)\n?\s*일부 위원은', minutes, re.MULTILINE)
    s1 = pos.start() if pos else -1
    pos = re.search('(.?외환.?국제금융\s?동향.?과 관련하여.*|\(나\) 외환.국제금융\s?(및 금융시장)?\s?동향)\n?\s*(일부 위원은|대부분의 위원들은)', minutes,re.MULTILINE)
    s2 = pos.start() if pos else -1
    pos = re.search('(.?금융시장\s?동향.?과 관련하여,?|\(다\) 금융시장\s?동향)\n?\s*일부 위원은', minutes, re.MULTILINE)
    s3 = pos.start() if pos else -1
    pos = re.search('((\((다|라)\) )?.?통화정책\s?방향.?에 관한 토론,?|이상과 같은 의견\s?교환을 바탕으로.*통화정책\s?방향.*에.*토론.*)\n?', minutes,re.MULTILINE)
    s4 = pos.start() if pos else -1
    pos = re.search('(\(4\) 정부측 열석자 발언.*)\n?', minutes, re.MULTILINE)
    s5 = pos.start() if pos else -1
    pos = re.search('(\(.*\) 한국은행 기준금리 결정에 관한 위원별 의견\s?개진|이상과 같은 토론에 이어 .* 관한 위원별 의견개진이 있었음.*)\n?', minutes,re.MULTILINE)
    s6 = pos.start() if pos else -1
    positer = re.finditer('(\(\s?.*\s?\) ()(심의결과|토의결론))\n?', minutes, re.MULTILINE)
    s7 = [pos.start() for pos in positer if pos.start() > s6]
    s7 = s7[0] if s7 else -1

    # 국내외 경제동향
    bos = s1
    eos = s2
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('(일부|대부분의) 위원들?은', section, re.MULTILINE)
    bos = pos.start() if pos else -1
    section = section[bos:] if bos >= 0 else section
    section1, section1_txt = tidy_sentences(section)

    # 외환․국제금융 동향
    bos = s2
    eos = s3 if s3 >= 0 else s4
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('(일부|대부분의) 위원들?은', section, re.MULTILINE)
    bos = pos.start() if pos else -1
    section = section[bos:] if bos >= 0 else section
    section2, section2_txt = tidy_sentences(section)
    #print(section)

    # 금융시장 동향
    bos = s3
    eos = s4
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('(일부|대부분의) 위원들?은', section, re.MULTILINE)
    bos = pos.start() if pos else -1
    section = section[bos:] if bos >= 0 else section
    section3, section3_txt = tidy_sentences(section)

    # 통화정책방향
    bos = s4
    eos = s5 if s5 >= 0 else s6 if s6 >= 0 else s7
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('(일부|대부분의) 위원들?은', section, re.MULTILINE)
    bos = pos.start() if pos else -1
    section = section[bos:] if bos >= 0 else section
    section4, section4_txt = tidy_sentences(section)

    # 위원별 의견 개진
    bos = s6
    eos = s7
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('(일부|대부분의) 위원들?은', section, re.MULTILINE)
    bos = pos.start() if pos else -1
    section = section[bos:] if bos >= 0 else section
    section5, section5_txt = tidy_sentences(section)

    # 정부측 열석자 발언
    bos = s5
    eos = s6
    section = minutes[bos:eos] if bos >= 0 or eos >= 0 else ''
    pos = re.search('정부측 열석자 발언', section, re.MULTILINE)
    bos = pos.end() + 1 if pos else -1
    section = section[bos:] if bos >= 0 else section
    section6, section6_txt = tidy_sentences(section)

    sections = ['Economic Situation', 'Foreign Currency', 'Financial Markets',
                'Monetary Policy', 'Participants’ Views', 'Government’s View']
    section_texts = (section1, section2, section3, section4, section5, section6)


    return sections, section_texts


In [2]:
def tidy_sentences(section):
    sentence_enders = re.compile(r'((?<=[함음됨임봄짐움])(\s*\n|\.|;)|(?<=다)\.)\s*')
    splits = list((m.start(), m.end()) for m in re.finditer(sentence_enders, section))
    starts = [0] + [i[1] for i in splits]
    ends = [i[0] for i in splits]
    sentences = [section[start:end] for start, end in zip(starts[:-1], ends)]
    for i, s in enumerate(sentences):
        sentences[i] = (s.replace('\n', ' ').replace(' ', ' ')) + '.'

    text = '\n'.join(sentences) if len(sentences) > 0 else ''
    return sentences, text



In [3]:
import pandas as pd
import numpy as np

mpb_csv_test = pd.read_csv('E:\\BOK\\text2\\ALL_MPB.csv',sep=" ")
mpb_csv_test

Unnamed: 0     MPBDate                                            content
0             0  2019-06-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
1             1  2019-05-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
2             2  2019-05-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
3             3  2019-04-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
4             4  2019-03-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
5             5  2019-02-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
6             6  2019-02-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
7             7  2019-01-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
8             8  2019-01-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
9             9  2018-12-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
10           10  2018-12-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
11           11  2018-12-06  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
12           12  2018-11-30  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
13           13  2018-11-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
14           14  2018-10-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
15           15  2018-09-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
16           16  2018-08-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
17           17  2018-07-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
18           18  2018-07-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
19           19  2018-06-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
20           20  2018-05-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
21           21  2018-04-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
22           22  2018-04-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
23           23  2018-03-29  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
24           24  2018-03-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
25           25  2018-02-27  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
26           26  2018-02-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
27           27  2018-01-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
28           28  2017-12-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
29           29  2017-12-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
..          ...         ...                                                ...
263         263  2006-10-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
264         264  2006-10-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
265         265  2006-09-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
266         266  2006-09-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
267         267  2006-08-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
268         268  2006-08-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
269         269  2006-08-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
270         270  2006-07-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
271         271  2006-06-22  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
272         272  2006-06-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
273         273  2006-05-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
274         274  2006-05-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
275         275  2006-04-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
276         276  2006-03-23  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
277         277  2006-03-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
278         278  2006-02-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
279         279  2006-01-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
280         280  2006-01-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
281         281  2006-01-05  \n\n\n\n\n\n\n\n\n\n\n\n\n

In [5]:
mpb_csv_test.loc[1]['content']

'\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n2019년도 제10차\n\n금융통화위원회(정기) 의사록\n\n한 국 은 행\n\n\n\n- 1 -\n\n1. 일 자 2019년 5월 31일(금)\n\n2. 장 소 금융통화위원회 회의실\n\n3. 출석위원 이 주 열 의 장 (총재)\n\n이 일 형 위 원\n\n조 동 철 위 원\n\n고 승 범 위 원\n\n신 인 석 위 원\n\n윤 면 식 위 원 (부총재)\n\n임 지 원 위 원\n\n4. 결석위원 없 음\n\n5. 참 여 자 장 호 현 감사 신 호 순 부총재보\n\n유 상 대 부총재보 정 규 일 부총재보\n\n서 봉 국 외자운용원장 이 환 석 조사국장\n\n신 운 경제연구원장 민 좌 홍 금융안정국장\n\n박 종 석 통화정책국장 이 상 형 금융시장국장\n\n이 승 헌 국제국장 김 현 기 공보관\n\n채 병 득 금융통화위원회실장 성 광 진 의사팀장\n\n6. 회의경과\n\n가. 의결안건\n\n〈의안 제19호 ― 통화정책방향〉\n\n( 1 ) 전일 개최된 동향보고회의에서 조사국장이 보고 제32호 - 국내외 경제\n\n동향 및 평가 , 국제국장이 보고 제33호 - 외환·국제금융 동향 , 그리고 금융시\n\n장국장이 보고 제34호 - 금융시장 동향 에 대하여 보고하였음.(보고내용 : 별첨)\n\n( 2 ) 본회의에서는 의장이 전일 보고내용을 접수하고 한국은행법 제28조에\n\n따라 의안 제19호 - 통화정책방향 을 상정하였음.\n\n\n\n- 2 -\n\n( 3 ) 위원 토의내용\n\n전일 개최된 동향보고회의에서는 다음과 같은 토의가 있었음.\n\n(가) 국내외 경제동향 및 평가\n\n일부 위원은 유로지역의 노동시장이 지표상으로 양호한 상황을 지속하고 있\n\n는데, 그 실상을 들여다보면 예전처럼 노동수요 증가에 따라 유휴노동력이 줄어\n\n들기보다는 일자리 나누기와 같은 사회적 합의(social contract)에 의해 노동시장의\n\n양적지

In [4]:
section=[]
for i in range(len(mpb_csv_test)):
    mpb_csv_test.loc[i]['content']
    m_date = mpb_csv_test.loc[i]['MPBDate']
    test = mpb_csv_test.loc[i]['content']
    sectest = preprocess_minutes(test)
    if (sectest[1][1] != [] or sectest[1][2] != []): 
        section.append({'Date':m_date,
                        'Section 2':sectest[1][1],
                        'Section 3':sectest[1][2]
                        })

In [ ]:
# sectest

In [3]:
# sectest[1][1] 
# sectest[1][2]

In [8]:
section

[{'Date': '2019-04-18',
  'Section 2': ['일부 위원은 금년 들어 은행을 통한 외화자금 유입과 함께 명목실효환율이  완만한 하락세를 이어가고 있다고 언급하면서, 후속 움직임을 예의주시할 필요가  있다고 당부하였음.',
   '또한 최근 일부 외은지점의 자금 조달·운용이 역외거래를 중  심으로 증가하고 있는데, 비록 그 가능성은 낮겠지만 만일 신용 및 유동성 리스  크가 크게 부각될 경우 국내 외환시장에 영향을 줄 수 있어 보인다고 언급하면서  관련부서의 견해를 물었음.',
   '이에 관련부서에서는 외국환은행의 역외계정은 원칙적으로 일반계정과 분리  되어 있으나, 위원이 언급한 리스크 요인을 염두에 두고 관련 동향에 대한 면밀  한 모니터링을 지속하겠다고 답변하였음.',
   '- 10 -  다른 일부 위원은 일부 외은지점의 경우 외채 증가속도가 다소 빠르며 만기  불일치도 커지고 있어 유의할 필요가 있다는 견해를 밝혔음.',
   '이에 관련부서에서는 아직까지 크게 우려할 상황은 아닌 것으로 보이지만, 일  부에서 공격적인 영업행태가 나타나고 있어 이를 주의 깊게 모니터링하고 있다고  언급하였음.',
   '이어서 동 위원은 금년 중 기업의 수익성이 어떨 것으로 보는지 관련부서에  질의하였음.',
   '이에 관련부서에서는 시장참가자들은 금년 중 주요 기업의 영업이익 증가율  이 마이너스(-)를 나타낼 것으로 전망하고 있는데, 최근 전기전자업종의 실적부진  등으로 전망의 마이너스 폭이 확대되고 있다고 답변하였음.',
   '이에 동 위원은 시장참가자들의 전망에는 일반적으로 상향 편의(upward bias)  가 있다는 점을 감안하면 실적이 전망을 하회할 가능성이 있다고 언급하였음.',
   '관련부서에서는 위원이 언급한 상향 편의 가능성을 염두에 두고 있으며, 다만  반도체의 부진이 하반기에는 완화되고 비IT 부문의 수익성도 지난해보다 개선될  것이라는 전망은 유지되고 있다고 답변하였음.',
   '다음으로 동 위원은 과거 장단

In [17]:
# section[1][1][0]

['Economic Situation',
 'Foreign Currency',
 'Financial Markets',
 'Monetary Policy',
 'Participants’ Views',
 'Government’s View']

In [23]:
# section[1][0]

'2019-05-31'

In [47]:
# section[i][1][1][1]

['일부 위원은 우리나라 경제가 일본경제  에 비해 더 나아질 특별한 요인이 없음에도 불구하고 최근 원/엔 환율이 지속적으  로 하락하는 이유를 물었으며, 이에 대해 관련부서에서는 위안화 절상시 동아시아  권 통화의 절상폭이 클 것이라는 기대로 원화나 대만달러가 엔/달러 환율의 상승  을 추수하지 못하고 국내 외환수급 면에서 공급우위 상태가 지속되고 있는 데다   국제 투자은행들이 엔/달러 환율 전망을 상향조정하고 있음에도 불구하고 원/달러   환율에 대한 조정은 아직 이루어지지 않고 있어 기업 등 시장참가자들의 기대도   원화 절상 쪽으로 편향되어 있는 데 기인한다고 설명하였음.',
 '- 6 -     동 위원은 환율이 중장기적으로 각국의 기초경제여건(fundamental)을 반영하  여 움직인다는 점을 감안할 때 현재의 원/엔 환율 하락은 일시적인 현상이며 장기  적으로 반전될 가능성이 있는 것으로 보인다는 견해를 밝혔으며, 이에 대해 관련  부서에서는 동 견해에 동의하면서 우리나라의 경우 시장규모가 작아 일시적인 외  부 충격에 의한 영향을 쉽게 받는다는 점을 설명하는 한편, 향후 우리나라와 미국  간 내외금리 역전이 나타나고 작년과 같은 대규모 외환 유입은 일어나지 않을 것  임을 감안할 때 원/엔 환율이 추가 하락할 여지는 점차 축소될 것으로 생각된다고   답변하였음.',
 '다른 일부 위원은 최근 유로지역의 경제성장 실적이 예상보다 저조한 가운  데 일각에서는 정책금리 인하론까지 대두되면서 유로화가 크게 절하되고 있다면  서 유로화의 달러화에 대한 흐름이 중장기적으로 변화하는 것으로 볼 수 있는지   물었으며, 이에 대해 관련부서에서는 국제 투자은행들이 달러화 대비 유로화 전망  을 기존의 강세에서 약세로 바꾸고 있으며 장기적으로 다시 강세로 반전되지는   않을 것이라는 의견이 지배적이라고 설명하였음.',
 '동 위원은 국내 금리가 현 수준에서 유지되고 미국 금리가 상승하는 가운  데 달러화 보유에 따른 환차익 기대가 형성될 경우 원화 강세에 대한

In [48]:
#section 잘 나누어 지는지 확인

# count2 = 0
# count3 = 0
# for i in range(len(section)):
#     print(str(i)+" "+section[i][0] +":")
#     if section[i][1][1][1] != []: #is not None:
#         print('section2 :'+ 'not None')
#         count2 += 1 
#     if section[i][1][1][2] != []: # 
#         print('section3 :'+ 'not None')
#         count3 += 1
    

0 2019-06-20:
1 2019-05-31:
2 2019-05-09:
3 2019-04-18:
section2 :not None
4 2019-03-28:
5 2019-02-28:
6 2019-02-14:
7 2019-01-24:
section2 :not None
8 2019-01-17:
9 2018-12-26:
10 2018-12-20:
11 2018-12-06:
12 2018-11-30:
section2 :not None
13 2018-11-08:
14 2018-10-18:
section2 :not None
15 2018-09-20:
16 2018-08-31:
section2 :not None
17 2018-07-26:
18 2018-07-12:
section2 :not None
19 2018-06-20:
20 2018-05-24:
section2 :not None
21 2018-04-26:
22 2018-04-12:
section2 :not None
23 2018-03-29:
24 2018-03-08:
25 2018-02-27:
section2 :not None
26 2018-02-08:
27 2018-01-18:
28 2017-12-28:
29 2017-12-14:
30 2017-12-07:
31 2017-11-30:
section2 :not None
32 2017-11-09:
33 2017-10-19:
section2 :not None
34 2017-09-21:
35 2017-08-31:
section2 :not None
36 2017-08-10:
37 2017-07-13:
section2 :not None
38 2017-06-22:
39 2017-05-25:
section2 :not None
40 2017-04-27:
41 2017-04-13:
section2 :not None
42 2017-03-23:
43 2017-02-23:
section2 :not None
44 2017-01-26:
45 2017-01-13:
section2 :not No

In [49]:
# print (count2) #2월 28일은 둘다 None 
# print (count3)

157
127


In [5]:
import pandas as pd
import numpy as np

df_section = pd.DataFrame(section)

In [6]:
df_section

Date                                          Section 2  \
0    2019-04-18  [일부 위원은 금년 들어 은행을 통한 외화자금 유입과 함께 명목실효환율이  완만한 ...   
1    2019-01-24  [일부 위원은 예대율 규제 변화에 따라 은행의 자금조달 및 운용 행태가 바뀌  게 ...   
2    2018-11-30  [일부 위원은 그동안 글로벌펀드와 패시브펀드의 규모가 크게 확대되어 우리  나라 자...   
3    2018-10-18  [일부 위원은 우리나라가 전반적으로 일상적인 수준의 변동성 확대에는 잘 대  처할 ...   
4    2018-08-31  [일부 위원은 글로벌 투자자금 흐름의 관점에서 우리나라의 상대적 입지에 대  해 살...   
5    2018-07-12  [일부 위원은 미·중 간 무역분쟁, 유로지역 정치불안 등이 국제금융시장에 미  치는...   
6    2018-05-24  [일부 위원은 최근의 미 달러화 강세가 추가적으로 진행될 경우 일부 취약국  에 국...   
7    2018-04-12  [일부 위원은 최근 국제금융시장에서 Libor금리가 급등하면서 글로벌 달러자금  의...   
8    2018-02-27  [일부 위원은 미국의 장기금리 상승에도 불구하고 달러화 약세기조가 지속되  고 있으...   
9    2017-11-30  [일부 위원은 최근 미국의 금융·경제상황을 보면 금년 12월 미 연준이 금리를  인...   
10   2017-10-19  [일부 위원은 최근 미국에서는 임금상승세가 확대되고 세제개혁에 대한 기대  감이 커...   
11   2017-08-31  [일부 위원은 미국의 금리 정상화 행보에도 불구하고 미 달러화가 약세기조를  지속하...   
12   2017-07-13  [일부 위원은 주요국에서는 성장과 고용이 회복국면의 정점을 향해 가고 있음., 에도...   
13   2017-05-25  [일부 위원은 최근 국제금융시장이 안정된 모습을 지속하는 가운데 국내금융  시장도 ...   
14   2017-04-13  [일부 위원은 3월 미 FOMC 회의의 의사록을 보면 연준의 만기도래 보유채권  에...   
15   2017-02-23  [일부 위원은 Yellen 미 연준 의장이 미국의 금리인상 지연은 바람직하지 않다 ...   
16   2017-01-13  [일부 위원은 미국의 시간당평균임금 상승률이 확대되고 있어 물가상승 압력  이 높아...   
17   2016-12-15  [일부 위원은 미국의 재정지출 확대, 보호무  역주의 강화 등으로 미 연준의 금리인...   
18   2016-11-11  [일부 위원은 미국의 대선 결과가 중국경제  와 국제유가에 미치는 영향에 대해 물었...   
19   2016-10-13  [일부 위원은 최근 주요국의 금융시장이 대  체로 안정적인 모습을 보이고 있지만 영...   
20   2016-09-09  [일부 위원은 우리나라는 달러화 유동성 사  정이 양호한 것으로 평가되지만 중국의 ...   
21   2016-08-11  [일부 위원은 7월 미국 고용지표 호조 등으  로 미국의 금리인상 재개 가능성에 대...   
22   2016-07-14  [일부 위원은 브렉시트로 인한 국제금융시장  의 불안심리 확산이 예상보다 제한적인 ...   
23   2016-06-09  [일부 위원은 미국 금리인상과 관련하여 가  장 우려되는 시나리오는 미국의 경기회복...   
24   2016-05-13  [일부 위원은 국내 통화정책 운영의 가장 중    - 7 -  요한 대외 리스크로 ...   
25   2016-04-19  [일부 위원은 최근 원화가치의 절상폭이 확  대되고 있는 가운데 미국 BHC(Ben...   
26   2016-03-10  [일부 위원은 지난 5년간 미 달러화대비 주  요국 통화의 흐름을 살펴보면 원화가치...   
27   2016-02-16  [일부 위원은 도이치은행의 최근 상황과 이  에 따른 시장의 영향에 대한 관련부서의...   
28   2016-01-14  [일부 위원은 우리 경제와 밀접한 관계를  맺고 있는 중국 경제의 불확실성이 상당기...   
29   2015-12-10  [일부 위원은 관련부서에서 유로지역의 마  이너스 금리 확대에 대한 평가와 전망을 ...   
..          ...                                                ...   
127  2007-10-11  [일부 위원은 당행의 스왑시장 참여로   재정거래유인이 상당폭 줄어들긴 했지만 여전...   
128  2007-09-07  [일부 위원은 우리나라에 유입된 엔 캐  리트레이드 자금 규모의 측정이 어렵다는 점...   
129  2007-08-09  [일부 위원은 미국의 서브프라임 모기  지 부실의 문제로 인해 국제금융시장에서 엔 ...   
130  2007-07-12  [일부 위원은 최근 금융기관의 단기외  화 차입규제 이후 금융 및 외환시장 동향에 ...   
131  2007-06-08  [일부 위원은 우리나라의 정부부채 및  대외부채의 증가, 국제유가 상승, 교역조건 ...   
132  2007-05-10  [일부 위원은 최근 일부에서 제시되고   있는 폐쇄형 뮤추얼펀드를 이용한 외환보유액...   
133  2007-04-12  [대부분의 위원들은 최근 수출업체의   선물환매도로 통화스왑금리가 국채수익률을 밑도...   
134  2007-03-08  [일부 위원은 원화의 국제화를 위해서  는 제도 정비와 함께 실제 거래가 뒷받침되어...   
135  2007-02-08  [일부 위원은 지난달 정부가 발표한 해  외투자 확대방안이 실행될 경우 환율안정과 ...   
136  2007-01-11  [일부 위원은 수출기업의 선물환매도로   촉발된 금리재정거래는 단기외채 증가, 시장...   
137  2006-12-07  [일부 위원은 최근 미 달러화 약세가   지속될 것이라는 국제투자은행들의 전망에 대...   
138  2006-11-09  [일부 위원은 최근 주요국 중앙은행들  이 외환보유액의 통화구성을 다변화하면서 엔화...   
139  2006-10-12  [일부 위원은 최근 원/엔 환율의 하락은   금년내 일본의 금리 인상 가능성이 점차...   
140  2006-09-07  [일부 위원은 최근 원화선물옵션의 시  카고상업거래소(CME: Chicago Mer...   
141  2006-08-10  [일부 위원은 최근 외화대출이 대폭 증  가하였는데 은행들이 외화대출 재원 마련을 ...   
142  2006-07-07  [일부 위원은 지난 6월말 외평채 가산  금리가 80bp에 이른 것이 북한의 미사일...   
143  2006-06-08  [일부 위원은 세계적인 긴축기조의 영향  으로 신흥시장(emerging market...   
144  2006-05-11  [일부 위원은 최근 은행들의 외화차입   확대가 환율하락 기대에 주로 기인한 것인지...   
145  2006-04-07  [일부 위원은 최근의 환율하락은 국내   수급사정의 변화 외에 시장참가자들의 정책금...   
146  2006-03-09  [일부 위원은 과거 사례를 보면 원화환  율은 엔화환율 및 위안화환율과 높은 상관관...   
147  2006-02-09  [일부 위원은 자본유입에 대해서는 관대  한 반면 자본유출에 대해서는 비교적 엄격한...   
148  2006-01-12  [일부 위원은 2002년부터 거의 예외 없  이 연초에는 원화의 강세 현상이 나타나...   
149  2005-12-08  [일부 위원은 금년 들어 달러화가 엔화  나 유로화에 대해 상당히 강세를 나타낸 것...   
150  2005-11-10  [일부 위원은 미 달러화에 대한 엔화 약  세가 지속될 것으로 보는지 물었으며, 이...   
151  2005-10-11  [일부 위원은 미국과 우리나라의 정책금  리 격차가 확대되고 있는 가운데 금년 두 ...   
152  2005-09-08  [일부 

In [172]:
len(mpb_csv_test)

293

In [183]:
df_section['Section 3'][130][0] #130 번째 문서의 0번째 인덱스 문장

'일부 위원은 ｢자본시장과 금융투자업에 관한   법률｣의 영향으로 은행의 저원가성 예금에서 CMA로의 자금이동이 더욱 진행될   경우 은행의 수익성이 저하될 가능성이 있다고 언급한 뒤,   금융기관간 수신경쟁에 따른 수신금리 상승이 대출금리 인상으로 이어지면 신용  상태가 양호하지 않은 중소기업이나 개인대출자의 부담이 증가하게 될 것이므로   향후 ｢자본시장과 금융투자업에 관한 법률｣의 시행이 금융기관이나 금융시장에   미치는 영향을 면밀히 점검해야 한다는 견해를 나타내었음.'

In [7]:
import pandas as pd
from ekonlpy.sentiment import MPCK

def text2ngram(text) :
    mpck = MPCK()
    tokens = mpck.tokenize(text)
    ngrams = mpck.ngramize(tokens)
       
    return tokens + ngrams

In [162]:
MPCK()

In [ ]:
text2ngram(df_section['Section 2'][0][2])

In [81]:
df_section['Section 2'][1][30]

'또한 주가하락 및 위험회피성향 확대에도 불구하고 회사채 신용  스프레드 상승이 제약된 데는 완화적 통화정책 지속으로 시중유동성이 풍부한 점  등이 작용하고 있는 것으로 보인다고 첨언하였음.'

In [8]:
def wngram(index,section_number): # index 번째의사록 ngram #section_number --> 2 or 3
    ngram = []
    for i in range(len(df_section['Section ' +str(section_number)][index])): # section 2 문장개수만큼당 [i] ngram for 문 돌면서 합침
        word_ngram = text2ngram(df_section['Section '+str(section_number)][index][i])
        for j in word_ngram:
            ngram.append(j)
    return ngram

In [189]:
wngram(50,3)# 50번째 의사록 의 section 3 ngram 

['혼합형/NNG',
 '금리/NNG',
 '대출/NNG',
 '호조/NNG',
 '은행/NNG',
 '입장/NNG',
 '고정/NNG',
 '금리/NNG',
 '대출/NNG',
 '인정/NNG',
 '되/XSV',
 '방침/NNG',
 '부응/NNG',
 '하/XSV',
 '측면/NNG',
 '있/VV',
 '수요자/NNG',
 '입장/NNG',
 '고정/NNG',
 '금리/NNG',
 '적용/NNG',
 '금리/NNG',
 '위험/NNG',
 '벗/VV',
 '있/VV',
 '장점/NNG',
 '있/VV',
 '기본/NNG',
 '바람직/NNG',
 '의견/NNG',
 '제시/NNG',
 '하/XSV',
 '혼합/NNG',
 '형/NNG',
 '금리/NNG',
 '대출/NNG',
 '금리/NNG',
 '순수/NNG',
 '변동/NNG',
 '금리/NNG',
 '대출/NNG',
 '금리/NNG',
 '낮/VA',
 '수준/NNG',
 '은행/NNG',
 '수익구조/NNG',
 '측면/NNG',
 '이러/NNG',
 '지속/NNG',
 '가능/NNG',
 '하/VV',
 '검토/NNG',
 '필요/NNG',
 '견해/NNG',
 '력/NNG',
 '하/XSV',
 '대해/VV',
 '혼합형/NNG',
 '금리/NNG',
 '대출/NNG',
 '금리/NNG',
 '더/MAG',
 '낮/VA',
 '은행/NNG',
 '고정/NNG',
 '금리/NNG',
 '대출비중/NNG',
 '높/VV',
 '위하/VV',
 '혼합형/NNG',
 '금리/NNG',
 '대출/NNG',
 '금리/NNG',
 '낮/VA',
 '가져가/VV',
 '결과/NNG',
 '당분간/MAG',
 '혼합형/NNG',
 '금리/NNG',
 '대출/NNG',
 '중심/NNG',
 '주택담보대출/NNG',
 '움직이/VV',
 '같/VA',
 '답변/NNG',
 '하/XSV',
 '고정/NNG',
 '금리/NNG',
 '적용/NNG',
 '중/NNG',
 '금리/NNG',
 '위험/NNG',
 '문제

In [21]:
def date_ngram():
    list_all_ngram=[]
    for i in range(len(df_section)):
        date_gram_section_2  = wngram(i,2)
        date_gram_section_3  = wngram(i,3)
        print(i)
        list_all_ngram.append(date_gram_section_2 + date_gram_section_3)
    return list_all_ngram

# list_all_ngram = date_ngram():

In [14]:
list_all_ngram[16]


['임금/NNG',
 '상승률/NNG',
 '확대/NNG',
 '되/XSV',
 '물가/NNG',
 '상승/NNG',
 '압력/NNG',
 '높/VA',
 '가능성/NNG',
 '있/VV',
 'fed/NNG',
 '조만간/MAG',
 '물가/NNG',
 '상승률/NNG',
 '목표/NNG',
 '수준/NNG',
 '도달/NNG',
 '하/VV',
 '보/VV',
 '추가/NNG',
 '확장/NNG',
 '재정정책/NNG',
 '필요/NNG',
 '않/VX',
 '입장/NNG',
 '보/VV',
 '언급/NNG',
 '하/XSV',
 '그럼에도/VA',
 '불구/NNG',
 '이러/NNG',
 '정책/NNG',
 '추진/NNG',
 '되/VV',
 'fed/NNG',
 '금리/NNG',
 '인상/NNG',
 '속도/NNG',
 '시장/NNG',
 '예상/NNG',
 '빠르/VA',
 '가능성/NNG',
 '있/VV',
 '의견/NNG',
 '나타나/VV',
 '물가/NNG;상승/NNG;압력/NNG;높/VA',
 '임금/NNG;상승률/NNG;확대/NNG',
 'fed/NNG;금리/NNG;인상/NNG',
 '대해/VV',
 '물가/NNG',
 '상승/NNG',
 '압력/NNG',
 '재정/NNG',
 '지출/NNG',
 '확대/NNG',
 '증대/NNG',
 '되/XSV',
 'fed/NNG',
 '금리/NNG',
 '인상/NNG',
 '속도/NNG',
 '예상/NNG',
 '빠르/VA',
 '관측/NNG',
 '제기/NNG',
 '되/XSV',
 '경제/NNG',
 '회복/NNG',
 '속도/NNG',
 '그만큼/MAG',
 '르/NNG',
 '않/VX',
 '있/VV',
 '재정/NNG',
 '지출/NNG',
 '확대/NNG',
 '하/XSV',
 '많/VA',
 '어렵/VV',
 '수반/NNG',
 '되/VV',
 '있/VV',
 '점/NNG',
 '전망/NNG',
 '유지/NNG',
 '하/XSV',
 '알/VV',
 '답변/NNG',
 '하/XSV',
 

In [11]:
len(list_all_ngram)

157

In [12]:
import pandas as pd
import numpy as np

# pd_ngram = pd.DataFrame(list_all_ngram ,index  ,colums = ['ngram'])
df_ngram=pd.DataFrame()
df_ngram['ngram']=list_all_ngram
df_ngram


ngram
0    [들/VV, 은행/NNG, 통하/VV, 외화자금/NNG, 유입/NNG, 함께/MAG...
1    [예대율/NNG, 규제/NNG, 변화/NNG, 은행/NNG, 자금/NNG, 조달/N...
2    [글로벌/NNG, 펀드/NNG, 패시브/NNG, 펀드/NNG, 규모/NNG, 크/V...
3    [일상/NNG, 수준/NNG, 변동성/NNG, 확대/NNG, 잘/MAG, 처/NNG...
4    [글로벌/NNG, 투자자금/NNG, 흐름/NNG, 관점/NNG, 상대적/VAX, 입...
5    [미/NNG, 중/NNG, 무역/NNG, 분쟁/NNG, 유로존/NNG, 정치/NNG...
6    [미/NNG, 달러/NNG, 강세/NNG, 추가/NNG, 진행/NNG, 되/VV, ...
7    [국제/NNG, 금융시장/NNG, 금리/NNG, 급등/NNG, 하/XSV, 글로벌/...
8    [장기/NNG, 금리/NNG, 상승/NNG, 불구/NNG, 달러/NNG, 약세/NN...
9    [금융경제/NNG, 보/VV, fed/NNG, 금리/NNG, 인상/NNG, 하/VV...
10   [임금/NNG, 상승/NNG, 확대/NNG, 되/XSV, 세제/NNG, 개혁/NNG...
11   [금리정상화/NNG, 행보/NNG, 불구/NNG, 미/NNG, 달러/NNG, 약세/...
12   [성장/NNG, 고용/NNG, 회복국면/NNG, 정점/NNG, 향하/VV, 불구/N...
13   [국제/NNG, 금융시장/NNG, 안정/NNG, 되/VV, 지속/NNG, 하/XSV...
14   [미/NNG, fed/NNG, 의사록/NNG, 보/VV, fed/NNG, 만기/NN...
15   [금리/NNG, 인상/NNG, 지연/NNG, 바람직/NNG, 않/VX, 언급/NNG...
16   [임금/NNG, 상승률/NNG, 확대/NNG, 되/XSV, 물가/NNG, 상승/NN...
17   [재정/NNG, 지출/NNG, 확대/NNG, 보호무역주의/NNG, 강화/NNG, f...
18   [대선/NNG, 결과/NNG, 경제/NNG, 오/VV, 국제/NNG, 유가/NNG,...
19   [금융시장/NNG, 체로/NNG, 안정/NNG, 보/VV, 예외적/VAX, 물가/N...
20   [달러/NNG, 유동성/NNG, 양호/NNG, 평가/NNG, 되/XSV, 어떠/NN...
21   [고용/NNG, 지표/NNG, 호조/NNG, 로/NNG, 금리/NNG, 인상/NNG...
22   [브렉시트/NNG, 인하/VV, 국제/NNG, 금융시장/NNG, 불안/NNG, 확산...
23   [금리/NNG, 인상/NNG, 가/VV, 장/NNG, 우려/NNG, 되/XSV, 시...
24   [통화정책/NNG, 운영/NNG, 가장/NNG, 중/NNG, 대외/NNG, 위험/N...
25   [원화/NNG, 절상/NNG, 확대/NNG, 되/XSV, 가운데/NNG, 법안/NN...
26   [미/NNG, 달러/NNG, 대비/NNG, 통화/NNG, 흐름/NNG, 살펴보/VV...
27   [따르/VV, 시장/NNG, 영향/NNG, 견해/NNG, 물/VV, 대해/VV, 부...
28   [경제/NNG, 밀접/NNG, 관계/NNG, 맺/VV, 경제/NNG, 불확실성/NN...
29   [유로존/NNG, 마이너스금리/NNG, 확대/NNG, 평가/NNG, 전망/NNG, ...
..                                                 ...
127  [당/NNG, 행의/NNG, 스왑/NNG, 시장/NNG, 참여/NNG, 재정거래/N...
128  [유입/NNG, 되/VV, 엔/NNG, 캐리/NNG, 자금/NNG, 규모/NNG, ...
129  [서브프라임/NNG, 부실/NNG, 문제/NNG, 인하/VV, 국제/NNG, 금융시...
130  [금융기관/NNG, 단기/NNG, 외화차입/NNG, 규제/NNG, 금융/NNG, 외...
131  [부채/NNG, 대외/NNG, 부채/NNG, 증가/NNG, 국제/NNG, 유가/NN...
132  [제시/NNG, 되/XSV, 폐쇄형/NNG, 뮤추얼펀드/NNG, 이용/NNG, 외환...
133  [수출업체/NNG, 선물환/NNG, 매도/NNG, crs/NNG, 금리/NNG, 국...
134  [원화/NNG, 국제화/NNG, 위하/VV, 는/VV, 제도/NNG, 정비/NNG,...
135  [발표/NNG, 하/VV, 해외/NNG, 투자/NNG, 확대/NNG, 방안/NNG,...
136  [수출기업/NNG, 선물환/NNG, 매도/NNG, 촉발/NNG, 되/VV, 금리재정...
137  [미/NNG, 달러/NNG, 약세/NNG, 지속/NNG, 되/VV, 국제투자은행/N...
138  [외환보유액/NNG, 통화/NNG, 구성/NNG, 다변화/NNG, 하/XSV, 엔/...
139  [원엔/NNG, 환율/NNG, 하락/NNG, 금리/NNG, 인상/NNG, 가능성/N...
140  [원화/NNG, 선물옵션/NNG, 시카고상업거래소/NNG, 상장/NNG, 원화/NN...
141  [외화대출/NNG, 대폭/MAG, 증/NNG, 가하/NNG, 은행/NNG, 외화대출...
142  [외평채/NNG, 스프레드/NNG, 이르/VA, 미사일/NNG, 발사/NNG, 영향...
143  [세계/NNG, 긴축/NNG, 기조/NNG, 영향/NNG, 신흥시장/NNG, 투자/...
144  [은행/NNG, 외화차입/NNG, 확대/NNG, 환율/NNG, 하락/NNG, 기대/...
145  [환율/NNG, 하락/NNG, 수급/NNG, 사정/NNG, 변화/NNG, 금리/NN...
146  [사례/NNG, 보/VV, 원화/NNG, 환율/NNG, 엔/NNG, 환율/NNG, ...
147  [자본/NNG, 유입/NNG, 대해서/VV, 관대/NNG, 반면/NNG, 자본/NN...
148  [거의/MAG, 예외/NNG, 없/VA, 원화/NNG, 강세/NNG, 현상/NNG,...
149  [들/VV, 달러/NNG, 엔/NNG, 유로/NNG, 대해/VV, 상당히/MAG, ...
150  [미/NNG, 달러/NNG, 엔/NNG, 약세/NNG, 지속/NNG, 되/VV, 보...
151  [금리갭/NNG, 확대/NNG, 되/XSV, 가운데/NNG, 남/VV, fed/NN...
152  [금융/NNG, 불안사태/NNG, 발생/NNG, 하/VV, 가운데/NNG, 국제/N...
153  [위안/NNG, 절상/NNG, 원화/NNG, 절상/NNG, 가장/MAG, 크/VA,...
154  [들/VV, 국제/NNG, 유가/NNG, 크/VA, 오르/VV, 원화/NNG, 엔/...
155  [경제/NNG, 경제/NNG, 비해/VV, 더/MAG, 낫/VV, 특별/NNG, 요...
156  [경제/NNG, 경제/NNG, 비해/VV, 더/MAG, 낫/VV, 특별/NNG, 요...

[157 rows x 1 columns]

In [95]:
# df['ngram'][0]

In [96]:
# ngram

In [ ]:
# m-gram합치기 /df_section /df
# df_section  d

In [15]:
df_Section_ngram = pd.concat([df_section, df_ngram],axis =1 )
df_Section_ngram

Date                                          Section 2  \
0    2019-04-18  [일부 위원은 금년 들어 은행을 통한 외화자금 유입과 함께 명목실효환율이  완만한 ...   
1    2019-01-24  [일부 위원은 예대율 규제 변화에 따라 은행의 자금조달 및 운용 행태가 바뀌  게 ...   
2    2018-11-30  [일부 위원은 그동안 글로벌펀드와 패시브펀드의 규모가 크게 확대되어 우리  나라 자...   
3    2018-10-18  [일부 위원은 우리나라가 전반적으로 일상적인 수준의 변동성 확대에는 잘 대  처할 ...   
4    2018-08-31  [일부 위원은 글로벌 투자자금 흐름의 관점에서 우리나라의 상대적 입지에 대  해 살...   
5    2018-07-12  [일부 위원은 미·중 간 무역분쟁, 유로지역 정치불안 등이 국제금융시장에 미  치는...   
6    2018-05-24  [일부 위원은 최근의 미 달러화 강세가 추가적으로 진행될 경우 일부 취약국  에 국...   
7    2018-04-12  [일부 위원은 최근 국제금융시장에서 Libor금리가 급등하면서 글로벌 달러자금  의...   
8    2018-02-27  [일부 위원은 미국의 장기금리 상승에도 불구하고 달러화 약세기조가 지속되  고 있으...   
9    2017-11-30  [일부 위원은 최근 미국의 금융·경제상황을 보면 금년 12월 미 연준이 금리를  인...   
10   2017-10-19  [일부 위원은 최근 미국에서는 임금상승세가 확대되고 세제개혁에 대한 기대  감이 커...   
11   2017-08-31  [일부 위원은 미국의 금리 정상화 행보에도 불구하고 미 달러화가 약세기조를  지속하...   
12   2017-07-13  [일부 위원은 주요국에서는 성장과 고용이 회복국면의 정점을 향해 가고 있음., 에도...   
13   2017-05-25  [일부 위원은 최근 국제금융시장이 안정된 모습을 지속하는 가운데 국내금융  시장도 ...   
14   2017-04-13  [일부 위원은 3월 미 FOMC 회의의 의사록을 보면 연준의 만기도래 보유채권  에...   
15   2017-02-23  [일부 위원은 Yellen 미 연준 의장이 미국의 금리인상 지연은 바람직하지 않다 ...   
16   2017-01-13  [일부 위원은 미국의 시간당평균임금 상승률이 확대되고 있어 물가상승 압력  이 높아...   
17   2016-12-15  [일부 위원은 미국의 재정지출 확대, 보호무  역주의 강화 등으로 미 연준의 금리인...   
18   2016-11-11  [일부 위원은 미국의 대선 결과가 중국경제  와 국제유가에 미치는 영향에 대해 물었...   
19   2016-10-13  [일부 위원은 최근 주요국의 금융시장이 대  체로 안정적인 모습을 보이고 있지만 영...   
20   2016-09-09  [일부 위원은 우리나라는 달러화 유동성 사  정이 양호한 것으로 평가되지만 중국의 ...   
21   2016-08-11  [일부 위원은 7월 미국 고용지표 호조 등으  로 미국의 금리인상 재개 가능성에 대...   
22   2016-07-14  [일부 위원은 브렉시트로 인한 국제금융시장  의 불안심리 확산이 예상보다 제한적인 ...   
23   2016-06-09  [일부 위원은 미국 금리인상과 관련하여 가  장 우려되는 시나리오는 미국의 경기회복...   
24   2016-05-13  [일부 위원은 국내 통화정책 운영의 가장 중    - 7 -  요한 대외 리스크로 ...   
25   2016-04-19  [일부 위원은 최근 원화가치의 절상폭이 확  대되고 있는 가운데 미국 BHC(Ben...   
26   2016-03-10  [일부 위원은 지난 5년간 미 달러화대비 주  요국 통화의 흐름을 살펴보면 원화가치...   
27   2016-02-16  [일부 위원은 도이치은행의 최근 상황과 이  에 따른 시장의 영향에 대한 관련부서의...   
28   2016-01-14  [일부 위원은 우리 경제와 밀접한 관계를  맺고 있는 중국 경제의 불확실성이 상당기...   
29   2015-12-10  [일부 위원은 관련부서에서 유로지역의 마  이너스 금리 확대에 대한 평가와 전망을 ...   
..          ...                                                ...   
127  2007-10-11  [일부 위원은 당행의 스왑시장 참여로   재정거래유인이 상당폭 줄어들긴 했지만 여전...   
128  2007-09-07  [일부 위원은 우리나라에 유입된 엔 캐  리트레이드 자금 규모의 측정이 어렵다는 점...   
129  2007-08-09  [일부 위원은 미국의 서브프라임 모기  지 부실의 문제로 인해 국제금융시장에서 엔 ...   
130  2007-07-12  [일부 위원은 최근 금융기관의 단기외  화 차입규제 이후 금융 및 외환시장 동향에 ...   
131  2007-06-08  [일부 위원은 우리나라의 정부부채 및  대외부채의 증가, 국제유가 상승, 교역조건 ...   
132  2007-05-10  [일부 위원은 최근 일부에서 제시되고   있는 폐쇄형 뮤추얼펀드를 이용한 외환보유액...   
133  2007-04-12  [대부분의 위원들은 최근 수출업체의   선물환매도로 통화스왑금리가 국채수익률을 밑도...   
134  2007-03-08  [일부 위원은 원화의 국제화를 위해서  는 제도 정비와 함께 실제 거래가 뒷받침되어...   
135  2007-02-08  [일부 위원은 지난달 정부가 발표한 해  외투자 확대방안이 실행될 경우 환율안정과 ...   
136  2007-01-11  [일부 위원은 수출기업의 선물환매도로   촉발된 금리재정거래는 단기외채 증가, 시장...   
137  2006-12-07  [일부 위원은 최근 미 달러화 약세가   지속될 것이라는 국제투자은행들의 전망에 대...   
138  2006-11-09  [일부 위원은 최근 주요국 중앙은행들  이 외환보유액의 통화구성을 다변화하면서 엔화...   
139  2006-10-12  [일부 위원은 최근 원/엔 환율의 하락은   금년내 일본의 금리 인상 가능성이 점차...   
140  2006-09-07  [일부 위원은 최근 원화선물옵션의 시  카고상업거래소(CME: Chicago Mer...   
141  2006-08-10  [일부 위원은 최근 외화대출이 대폭 증  가하였는데 은행들이 외화대출 재원 마련을 ...   
142  2006-07-07  [일부 위원은 지난 6월말 외평채 가산  금리가 80bp에 이른 것이 북한의 미사일...   
143  2006-06-08  [일부 위원은 세계적인 긴축기조의 영향  으로 신흥시장(emerging market...   
144  2006-05-11  [일부 위원은 최근 은행들의 외화차입   확대가 환율하락 기대에 주로 기인한 것인지...   
145  2006-04-07  [일부 위원은 최근의 환율하락은 국내   수급사정의 변화 외에 시장참가자들의 정책금...   
146  2006-03-09  [일부 위원은 과거 사례를 보면 원화환  율은 엔화환율 및 위안화환율과 높은 상관관...   
147  2006-02-09  [일부 위원은 자본유입에 대해서는 관대  한 반면 자본유출에 대해서는 비교적 엄격한...   
148  2006-01-12  [일부 위원은 2002년부터 거의 예외 없  이 연초에는 원화의 강세 현상이 나타나...   
149  2005-12-08  [일부 위원은 금년 들어 달러화가 엔화  나 유로화에 대해 상당히 강세를 나타낸 것...   
150  2005-11-10  [일부 위원은 미 달러화에 대한 엔화 약  세가 지속될 것으로 보는지 물었으며, 이...   
151  2005-10-11  [일부 위원은 미국과 우리나라의 정책금  리 격차가 확대되고 있는 가운데 금년 두 ...   
152  2005-09-08  [일부 

In [16]:
df_Section_ngram.columns = ['date','Section 2','Section 3','n-gram']

In [17]:
call = pd.read_csv('E:\\call_rate.csv',sep=" ")

In [110]:
call

date   콜금리   Before 1M  1달 전 콜금리                    전달대비  label
0     2017-12-31  1.58  2017-11-30      1.53  +0.050000000000000044%      1
1     2017-12-30  1.58  2017-11-30      1.53  +0.050000000000000044%      1
2     2017-12-29  1.58  2017-11-29      1.26   +0.32000000000000006%      1
3     2017-12-28  1.55  2017-11-28      1.26   +0.29000000000000004%      1
4     2017-12-27  1.51  2017-11-27      1.26                  +0.25%      1
5     2017-12-26  1.52  2017-11-26      1.26                  +0.26%      1
6     2017-12-25  1.52  2017-11-25      1.26                  +0.26%      1
7     2017-12-24  1.52  2017-11-24      1.25                  +0.27%      1
8     2017-12-23  1.52  2017-11-23      1.25                  +0.27%      1
9     2017-12-22  1.51  2017-11-22      1.24                  +0.27%      1
10    2017-12-21  1.53  2017-11-21      1.25                  +0.28%      1
11    2017-12-20  1.51  2017-11-20      1.25                  +0.26%      1
12    2017-12-19  1.50  2017-11-19      1.25                  +0.25%      1
13    2017-12-18  1.50  2017-11-18      1.25                  +0.25%      1
14    2017-12-17  1.50  2017-11-17      1.24                  +0.26%      1
15    2017-12-16  1.50  2017-11-16      1.24                  +0.26%      1
16    2017-12-15  1.51  2017-11-15      1.24                  +0.27%      1
17    2017-12-14  1.50  2017-11-14      1.24                  +0.26%      1
18    2017-12-13  1.50  2017-11-13      1.25                  +0.25%      1
19    2017-12-12  1.51  2017-11-12      1.25                  +0.26%      1
20    2017-12-11  1.52  2017-11-11      1.25                  +0.27%      1
21    2017-12-10  1.52  2017-11-10      1.24                  +0.28%      1
22    2017-12-09  1.52  2017-11-09      1.24                  +0.28%      1
23    2017-12-08  1.52  2017-11-08      1.23   +0.29000000000000004%      1
24    2017-12-07  1.49  2017-11-07      1.25                  +0.24%      1
25    2017-12-06  1.48  2017-11-06      1.23                  +0.25%      1
26    2017-12-05  1.47  2017-11-05      1.23                  +0.24%      1
27    2017-12-04  1.48  2017-11-04      1.23                  +0.25%      1
28    2017-12-03  1.48  2017-11-03      1.24                  +0.24%      1
29    2017-12-02  1.48  2017-11-02      1.24                  +0.24%      1
...          ...   ...         ...       ...                     ...    ...
4718  2005-01-30  3.26  2004-12-30      0.00                  +3.26%      1
4719  2005-01-29  3.26  2004-12-29      0.00                  +3.26%      1
4720  2005-01-28  3.25  2004-12-28      0.00                  +3.25%      1
4721  2005-01-27  3.24  2004-12-27      0.00                  +3.24%      1
4722  2005-01-26  3.26  2004-12-26      0.00                  +3.26%      1
4723  2005-01-25  3.25  2004-12-25      0.00                  +3.25%      1
4724  2005-01-24  3.25  2004-12-24      0.00                  +3.25%      1
4725  2005-01-23  3.25  2004-12-23      0.00                  +3.25%      1
4726  2005-01-22  3.25  2004-12-22      0.00                  +3.25%      1
4727  2005-01-21  3.19  2004-12-21      0.00                  +3.19%      1
4728  2005-01-20  3.23  2004-12-20      0.00                  +3.23%      1
4729  2005-01-19  3.25  2004-12-19      0.00                  +3.25%      1
4730  2005-01-18  3.25  2004-12-18      0.00                  +3.25%      1
4731  2005-01-17  3.25  2004-12-17      0.00                  +3.25%      1
4732  2005-01-16  3.25  2004-12-16      0.00                  +3.25%      1
4733  2005-01-15  3.25  2004-12-15      0.00                  +3.25%      1
4734  2005-01-14  3.26  2004-12-14      0.00                  +3.26%      1
4735  2005-01-13  3.28  2004-12-13      0.00                  +3.28%      1
4736  2005-01-12  3.27  2004-12-12      0.00                  +3.27%      1
4737  2005-01-11  3.28  2004-12-11      0.00                  +3.28%      1
4738  2005-01-10  3.27  2004-12-10      0.00                

In [ ]:
#콜금리 pos 합치기

In [ ]:
# pd.concat([df_Section_ngram,call],axis = 1)

In [18]:
df_call_MPB = pd.merge(df_Section_ngram,call, on = "date", how = "left")

In [19]:
MPB_test=df_call_MPB[['date','n-gram','label']][9:]
MPB_test

date                                             n-gram  label
9    2017-11-30  [금융경제/NNG, 보/VV, fed/NNG, 금리/NNG, 인상/NNG, 하/VV...    1.0
10   2017-10-19  [임금/NNG, 상승/NNG, 확대/NNG, 되/XSV, 세제/NNG, 개혁/NNG...    0.0
11   2017-08-31  [금리정상화/NNG, 행보/NNG, 불구/NNG, 미/NNG, 달러/NNG, 약세/...    1.0
12   2017-07-13  [성장/NNG, 고용/NNG, 회복국면/NNG, 정점/NNG, 향하/VV, 불구/N...    1.0
13   2017-05-25  [국제/NNG, 금융시장/NNG, 안정/NNG, 되/VV, 지속/NNG, 하/XSV...   -1.0
14   2017-04-13  [미/NNG, fed/NNG, 의사록/NNG, 보/VV, fed/NNG, 만기/NN...    0.0
15   2017-02-23  [금리/NNG, 인상/NNG, 지연/NNG, 바람직/NNG, 않/VX, 언급/NNG...    0.0
16   2017-01-13  [임금/NNG, 상승률/NNG, 확대/NNG, 되/XSV, 물가/NNG, 상승/NN...    1.0
17   2016-12-15  [재정/NNG, 지출/NNG, 확대/NNG, 보호무역주의/NNG, 강화/NNG, f...   -1.0
18   2016-11-11  [대선/NNG, 결과/NNG, 경제/NNG, 오/VV, 국제/NNG, 유가/NNG,...   -1.0
19   2016-10-13  [금융시장/NNG, 체로/NNG, 안정/NNG, 보/VV, 예외적/VAX, 물가/N...   -1.0
20   2016-09-09  [달러/NNG, 유동성/NNG, 양호/NNG, 평가/NNG, 되/XSV, 어떠/NN...    1.0
21   2016-08-11  [고용/NNG, 지표/NNG, 호조/NNG, 로/NNG, 금리/NNG, 인상/NNG...    0.0
22   2016-07-14  [브렉시트/NNG, 인하/VV, 국제/NNG, 금융시장/NNG, 불안/NNG, 확산...   -1.0
23   2016-06-09  [금리/NNG, 인상/NNG, 가/VV, 장/NNG, 우려/NNG, 되/XSV, 시...   -1.0
24   2016-05-13  [통화정책/NNG, 운영/NNG, 가장/NNG, 중/NNG, 대외/NNG, 위험/N...    0.0
25   2016-04-19  [원화/NNG, 절상/NNG, 확대/NNG, 되/XSV, 가운데/NNG, 법안/NN...   -1.0
26   2016-03-10  [미/NNG, 달러/NNG, 대비/NNG, 통화/NNG, 흐름/NNG, 살펴보/VV...    1.0
27   2016-02-16  [따르/VV, 시장/NNG, 영향/NNG, 견해/NNG, 물/VV, 대해/VV, 부...   -1.0
28   2016-01-14  [경제/NNG, 밀접/NNG, 관계/NNG, 맺/VV, 경제/NNG, 불확실성/NN...    1.0
29   2015-12-10  [유로존/NNG, 마이너스금리/NNG, 확대/NNG, 평가/NNG, 전망/NNG, ...   -1.0
30   2015-11-12  [수출/NNG, 감소/NNG, 지속/NNG, 되/XSV, 실질/NNG, 실효환율/N...    1.0
31   2015-10-15  [이어지/VV, 원달러/NNG, 상승/NNG, 주춤/NNG, 언급/NNG, 하/VV...   -1.0
32   2015-09-11  [원달러/NNG, 크/VA, 상/NNG, 승한/VV, 위안화예금/NNG, 중심/NN...    0.0
33   2015-08-13  [위안/NNG, 절하/NNG, 시장/NNG, 평가/NNG, 질의/NNG, 하/XSV...    1.0
34   2015-07-09  [그리스사태/NNG, 금리/NNG, 인상/NNG, 영향/NNG, 미치/VV, 보/V...   -1.0
35   2015-06-11  [질의/NNG, 통/MAG, 민간/NNG, 해외/NNG, 투자/NNG, 촉진/NNG...   -1.0
36   2015-05-15  [아베노믹스/NNG, 경제/NNG, 미치/VV, 파장/NNG, 예상/NNG, 크/V...    1.0
37   2015-04-09  [국/NNG, 외국인/NNG, 채권투자/NNG, 비중/NNG, 보/VV, 높/VA,...   -1.0
38   2015-03-12  [원달러/NNG, 상보/NNG, 다/MAG, 빠르/VA, 상승/NNG, 하/VV, ...   -1.0
..          ...                                                ...    ...
127  2007-10-11  [당/NNG, 행의/NNG, 스왑/NNG, 시장/NNG, 참여/NNG, 재정거래/N...    1.0
128  2007-09-07  [유입/NNG, 되/VV, 엔/NNG, 캐리/NNG, 자금/NNG, 규모/NNG, ...    1.0
129  2007-08-09  [서브프라임/NNG, 부실/NNG, 문제/NNG, 인하/VV, 국제/NNG, 금융시...    1.0
130  2007-07-12  [금융기관/NNG, 단기/NNG, 외화차입/NNG, 규제/NNG, 금융/NNG, 외...    1.0
131  2007-06-08  [부채/NNG, 대외/NNG, 부채/NNG, 증가/NNG, 국제/NNG, 유가/NN...   -1.0
132  2007-05-10  [제시/NNG, 되/XSV, 폐쇄형/NNG, 뮤추얼펀드/NNG, 이용/NNG, 외환...    1.0
133  2007-04-12  [수출업체/NNG, 선물환/NNG, 매도/NNG, crs/NNG, 금리/NNG, 국...    1.0
134  2007-03-08  [원화/NNG, 국제화/NNG, 위하/VV, 는/VV, 제도/NNG, 정비/NNG,...    0.0
135  2007-02-08  [발표/NNG, 하/VV, 해외/NNG, 투자/NNG, 확대/NNG, 방안/NNG,...   -1.0
136  2007-01-11  [수출기업/NNG, 선물환/NNG, 매도/NNG, 촉발/NNG, 되/VV, 금리재정...    1.0
137  2006-12-07  [미/NNG, 달러/NNG, 약세/NNG, 지속/NNG, 되/VV, 국제투자은행/N...   -1.0
138  2006-11-09  [외환보유액/NNG, 통화/NNG, 구성/NNG, 다변화/NNG, 하/XSV, 엔/...    0.0
139  2006-10-12  [원엔/NNG, 환율/NNG, 하락/NNG, 금리/NNG, 인상/NNG, 가능성/N...    1.0
140  2006-09-07  [원화/NNG, 선물옵션/NNG, 시카고상업거래소/NNG, 상장/NNG, 원화/NN...    1.0
141  2006-08-10  [외화대출/NNG, 대폭/MAG, 증/NNG, 가하/NNG, 은행/NNG, 외화대출...    1.0
142  2006-07-07  [외평채/NNG, 스프레드/NNG, 이르/VA, 미사일/NNG, 발사/NNG, 영향...    1.0
143  2006-06-08  [세계/NNG, 긴축/NNG, 기조/NNG, 영향/NNG, 신흥시장/NNG, 투자/...    1.0
144  2006-05-11  [은행/NNG, 외화차입/NNG, 확대/NNG, 환율/NNG, 하락/NNG, 기대/...    0.0
145  2006-04-07  [환율/NNG, 하락/NNG, 수급/NNG, 사정/NNG, 변화/NNG, 금리/NN...   -1.0
146  2006-03-09  [사례/NNG, 보/VV, 원화/NNG, 환율/NNG, 엔/NNG, 환율/NNG, ...   -1.0
147  2006-02-09  [자본/NNG, 유입/NNG, 대해서/VV, 관대/NNG, 반면/NNG, 자본/NN...    1.0
148  2006-01-12  [거의/MAG, 예외/NNG, 없/VA, 원화/NNG, 강세/NNG, 현상/NNG,...    0.0
149  2005-12-08

In [20]:
MPB_test.to_csv('E:\\BOK\\text2\\MPB_mgram_call.csv',sep= " ") #csv 로 저장

In [22]:
df_MPB= pd.read_csv('E:\\BOK\\text2\\MPB_mgram_call.csv',sep= " ") #csv로 다시 불러오기

In [23]:
df_MPB

Unnamed: 0        date  \
0             9  2017-11-30   
1            10  2017-10-19   
2            11  2017-08-31   
3            12  2017-07-13   
4            13  2017-05-25   
5            14  2017-04-13   
6            15  2017-02-23   
7            16  2017-01-13   
8            17  2016-12-15   
9            18  2016-11-11   
10           19  2016-10-13   
11           20  2016-09-09   
12           21  2016-08-11   
13           22  2016-07-14   
14           23  2016-06-09   
15           24  2016-05-13   
16           25  2016-04-19   
17           26  2016-03-10   
18           27  2016-02-16   
19           28  2016-01-14   
20           29  2015-12-10   
21           30  2015-11-12   
22           31  2015-10-15   
23           32  2015-09-11   
24           33  2015-08-13   
25           34  2015-07-09   
26           35  2015-06-11   
27           36  2015-05-15   
28           37  2015-04-09   
29           38  2015-03-12   
..          ...         ...   
118         127  2007-10-11   
119         128  2007-09-07   
120         129  2007-08-09   
121         130  2007-07-12   
122         131  2007-06-08   
123         132  2007-05-10   
124         133  2007-04-12   
125         134  2007-03-08   
126         135  2007-02-08   
127         136  2007-01-11   
128         137  2006-12-07   
129         138  2006-11-09   
130         139  2006-10-12   
131         140  2006-09-07   
132         141  2006-08-10   
133         142  2006-07-07   
134         143  2006-06-08   
135         144  2006-05-11   
136         145  2006-04-07   
137         146  2006-03-09   
138         147  2006-02-09   
139         148  2006-01-12   
140         149  2005-12-08   
141         150  2005-11-10   
142         151  2005-10-11   
143         152  2005-09-08   
144         153  2005-08-11   
145         154  2005-07-07   
146         155  2005-06-09   
147         156  2005-06-09   

                                                n-gram  label  
0    ['금융경제/NNG', '보/VV', 'fed/NNG', '금리/NNG', '인상/...    1.0  
1    ['임금/NNG', '상승/NNG', '확대/NNG', '되/XSV', '세제/NN...    0.0  
2    ['금리정상화/NNG', '행보/NNG', '불구/NNG', '미/NNG', '달러...    1.0  
3    ['성장/NNG', '고용/NNG', '회복국면/NNG', '정점/NNG', '향하...    1.0  
4    ['국제/NNG', '금융시장/NNG', '안정/NNG', '되/VV', '지속/N...   -1.0  
5    ['미/NNG', 'fed/NNG', '의사록/NNG', '보/VV', 'fed/N...    0.0  
6    ['금리/NNG', '인상/NNG', '지연/NNG', '바람직/NNG', '않/V...    0.0  
7    ['임금/NNG', '상승률/NNG', '확대/NNG', '되/XSV', '물가/N...    1.0  
8    ['재정/NNG', '지출/NNG', '확대/NNG', '보호무역주의/NNG', '...   -1.0  
9    ['대선/NNG', '결과/NNG', '경제/NNG', '오/VV', '국제/NNG...   -1.0  
10   ['금융시장/NNG', '체로/NNG', '안정/NNG', '보/VV', '예외적/...   -1.0  
11   ['달러/NNG', '유동성/NNG', '양호/NNG', '평가/NNG', '되/X...    1.0  
12   ['고용/NNG', '지표/NNG', '호조/NNG', '로/NNG', '금리/NN...    0.0  
13   ['브렉시트/NNG', '인하/VV', '국제/NNG', '금융시장/NNG', '불...   -1.0  
14   ['금리/NNG', '인상/NNG', '가/VV', '장/NNG', '우려/NNG'...   -1.0  
15   ['통화정책/NNG', '운영/NNG', '가장/NNG', '중/NNG', '대외/...    0.0  
16   ['원화/NNG', '절상/NNG', '확대/NNG', '되/XSV', '가운데/N...   -1.0  
17   ['미/NNG', '달러/NNG', '대비/NNG', '통화/NNG', '흐름/NN...    1.0  
18   ['따르/VV', '시장/NNG', '영향/NNG', '견해/NNG', '물/VV'...   -1.0  
19   ['경제/NNG', '밀접/NNG', '관계/NNG', '맺/VV', '경제/NNG...    1.0  
20   ['유로존/NNG', '마이너스금리/NNG', '확대/NNG', '평가/NNG', ...   -1.0  
21   ['수출/NNG', '감소/NNG', '지속/NNG', '되/XSV', '실질/NN...    1.0  
22   ['이어지/VV', '원달러/NNG', '상승/NNG', '주춤/NNG', '언급/...   -1.0  
23   ['원달러/NNG', '크/VA', '상/NNG', '승한/VV', '위안화예금/N...    0.0  
24   ['위안/NNG', '절하/NNG', '시장/NNG', '평가/NNG', '질의/N...    1.0  
25   ['그리스사태/NNG', '금리/NNG', '인상/NNG', '영향/NNG', '미...   -1.0  
26   ['질의/NNG', '통/MAG', '민간/NNG', '해외/NNG', '투자/NN...   -1.0  
27   ['아베노믹스/NNG', '경제/NNG', '미치/VV', '파장/NNG', '예상...    1.0  
28   ['국/NNG', '외국인/NNG', '채권투자/NNG', '비중/NNG', '보/...   -1.0  
29   ['원달러/NNG', '상보/NNG', '다/MAG', '빠르/VA', '상승/NN...   -1.0  
..                                                 ...    ...  
118  ['당/NNG', '행의/NNG', '스왑/NNG',